In [1]:
import altair as alt
import pandas as pd
import math
import matplotlib.pyplot as plt
import numpy as np
import dill
import datetime
from datetime import timedelta
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from mpl_toolkits.mplot3d import Axes3D
from ipywidgets import IntSlider
from ipywidgets import interact
from matplotlib import pylab as plt

In [4]:
#df_pan = pd.read_csv('medical.csv', low_memory=False)
#dill.dump(df_pan, open('df_pan.pkd', 'wb'))
df_prepan = pd.read_csv('Prepandemic_v2.csv')
df_pan = dill.load(open('df_pan.pkd', 'rb'))
df_pan_cases = pd.read_csv('casesAndDeaths.csv')
df_poverty = pd.read_csv('PovertyEstimates.csv')
df_pop = pd.read_csv('PopulationEstimates.csv')
df_policy = pd.read_csv('policy.csv')
df_county_cases = pd.read_csv('us-counties-covid.csv')

In [5]:
#rename columns for df_policy
df_policy = df_policy.rename(columns={'Date closed K-12 public schools': 'Schools Closed', 
                         'Mandate face mask use by all individuals in public spaces': 'Mask Mandate', 
                         'Closed restaurants except take out':'Restaurants Closed'})
columns = ['stname','ctyname','fips','Stay at home/ shelter in place','Schools Closed', 'Mask Mandate', 'Restaurants Closed']
df_policy = df_policy[columns]

df_pop = df_pan[['fips','POP_ESTIMA']]

df_posInc_policy = df_policy.merge(df_pop, on = 'fips') \
                            .merge(df_pan_cases, on = ['stname','ctyname','fips'])
df_posInc_policy = df_posInc_policy.drop(columns=['Unnamed: 0','stfips','ctyfips'], axis=1)


In [6]:
columns1 = (['FIPS','stname','ctyname_x', 'tot_2018', 'popdensity_2018'])
df_prepan = df_prepan[columns1]

columns2 = (['FIPStxt','PCTPOVALL_2019'])
df_poverty = df_poverty[columns2].rename(columns={'FIPStxt': 'FIPS', 'PCTPOVALL_2019': 'PCT_POV'})

df_prepan_pov = pd.merge(df_prepan, df_poverty, on='FIPS')

columns3 = (['fips','AgedPop','TotalPop'])
df_age = df_pan[columns3].rename(columns={'fips': 'FIPS'})
df_age['PCT_AGED'] = df_age['AgedPop']/ df_age['TotalPop']
df_age = df_age[(['FIPS','PCT_AGED'])]

df_prepan_pov_age = pd.merge(df_prepan_pov, df_age, on='FIPS')


FIPS   stname       ctyname_x  tot_2018  popdensity_2018  PCT_POV  PCT_AGED
0  1001  Alabama  Autauga County     55601        36.113876     12.1  0.145833
1  1003  Alabama  Baldwin County    218022        52.949490     10.1  0.195404
2  1005  Alabama  Barbour County     24881        10.854899     27.1  0.179738

In [104]:
dill.dump(df_posInc_policy, open('df_posInc_policy.pkd', 'wb'))

In [123]:
def intervention_effect(row_idx, intervention):
    try: 
        row_county_fips = df_posInc_policy['fips'][row_idx]
        row_event_date = df_posInc_policy[intervention][row_idx]
        row_event_date = datetime.datetime.strptime(row_event_date, '%Y/%m/%d')
#         print("Row event date: ", row_event_date)
        pre_window_start = row_event_date - timedelta(days = 7)
        post_window_start = row_event_date + timedelta(days = 14) # 3 weeks after intervention
        post_window_end = row_event_date + timedelta(days = 21) # 3 weeks after intervention
#         print('pre_window_start: ', pre_window_start)
#         print('post_window_start: ', post_window_start)
#         print('post_window_end: ',  post_window_end)
        
        row_event_date_str = datetime.datetime.strftime(row_event_date, '%Y%m%d')
        pre_window_start_str = datetime.datetime.strftime(pre_window_start, '%Y%m%d')
        post_window_start_str = datetime.datetime.strftime(post_window_start, '%Y%m%d')
        post_window_end_str = datetime.datetime.strftime(post_window_end, '%Y%m%d')
        
        col_row_event_date = 'confirmed_cases_{}'.format(row_event_date_str)
        col_pre_window_start = 'confirmed_cases_{}'.format(pre_window_start_str)
        col_post_window_start = 'confirmed_cases_{}'.format(post_window_start_str)
        col_post_window_end = 'confirmed_cases_{}'.format(post_window_end_str)
        
        try: 
            totalCases_preDay1 = df_posInc_policy.loc[row_idx,col_pre_window_start]
#             print('totalCases_preDay1: ', totalCases_preDay1)
            totalCases_preDay7 = df_posInc_policy.loc[row_idx,col_row_event_date]
#             print('totalCases_preDay7: ', totalCases_preDay7)
            total_county_pop = df_posInc_policy['POP_ESTIMA'][row_idx]
            pre_rolling7DayAvg_increase = ((totalCases_preDay7 - totalCases_preDay1)*1000) / (7*total_county_pop)
#             print('pre_rolling7DayAvg_increase: ', pre_rolling7DayAvg_increase)
        except: 
            pre_rolling7DayAvg_increase = None
#             print(f"Failed on PRE block: {row_county_fips}")

        try:
            totalCases_postDay1 = df_posInc_policy.loc[row_idx,col_post_window_start]
            totalCases_postDay7 = df_posInc_policy.loc[row_idx,col_post_window_end]
            total_county_pop = df_pan['POP_ESTIMA'][row_idx]
            post_rolling7DayAvg_increase = ((totalCases_postDay7 - totalCases_postDay1)*1000) / (7*total_county_pop)
#             print('post_rolling7DayAvg_increase: ', post_rolling7DayAvg_increase)
        except: 
#             print(f"Failed on POST block: {row_county_fips}")
            post_rolling7DayAvg_increase = None

        try: 
            diff = pre_rolling7DayAvg_increase - post_rolling7DayAvg_increase
#             print('diff: ', diff)
        except: 
#             print(f"Failed on DIFF block: {row_county_fips}")
            diff = None

        return diff
    except: 
#         print(f"Failed at top-level block: {row_county_fips}")
        return None
    

########################################################################################

def createPrePostDiffCol(intervention):
    diffs = []
    for i in range(len(df_pan)):
        diff = intervention_effect(i, intervention)
        diffs.append(diff)
    col_name = 'pre_post_diff_{}'.format(intervention)
    df = pd.DataFrame(diffs, columns = [col_name])
    return df

In [124]:
interventions = ['Mask Mandate', 'Stay at home/ shelter in place', 'Restaurants Closed']
for i in interventions: 
    col_name = 'pre_post_diff_{}'.format(i)
    df_posInc_policy[col_name] = createPrePostDiffCol(i)

<ipython-input-123-be050f94e1d3>:30: RuntimeWarning: invalid value encountered in longlong_scalars
  pre_rolling7DayAvg_increase = ((totalCases_preDay7 - totalCases_preDay1)*1000) / (7*total_county_pop)
<ipython-input-123-be050f94e1d3>:40: RuntimeWarning: invalid value encountered in longlong_scalars
  post_rolling7DayAvg_increase = ((totalCases_postDay7 - totalCases_postDay1)*1000) / (7*total_county_pop)


In [126]:
columns = (['stname', 'ctyname', 'fips', 'Stay at home/ shelter in place',
       'Schools Closed', 'Mask Mandate', 'Restaurants Closed','pre_post_diff_Mask Mandate',
       'pre_post_diff_Stay at home/ shelter in place',
       'pre_post_diff_Restaurants Closed'])
df_interv_diff = df_posInc_policy[columns]


stname         ctyname  fips Stay at home/ shelter in place  \
0  Alabama  Autauga County  1001                       2020/4/4   
1  Alabama  Baldwin County  1003                       2020/4/4   
2  Alabama  Barbour County  1005                       2020/4/4   

  Schools Closed Mask Mandate Restaurants Closed  pre_post_diff_Mask Mandate  \
0      2020/3/20    2020/7/16          2020/3/19                    0.077080   
1      2020/3/20    2020/7/16          2020/3/19                    0.066835   
2      2020/3/20    2020/7/16          2020/3/19                    0.287081   

   pre_post_diff_Stay at home/ shelter in place  \
0                                     -0.012847   
1                                     -0.019002   
2                                     -0.074641   

   pre_post_diff_Restaurants Closed  
0                         -0.012847  
1                         -0.021623  
2                         -0.045933

In [127]:
df_interv_diff.to_pickle("./df_interv_diff.pkl")

In [26]:
#df_prepan_pov_age.to_pickle("./df_prepan_pov_age.pkl")

## Checkpoint

Note: The above preprocessing code is not needed in final app version. 

In [131]:
df_interv_diff = pd.read_pickle("./df_interv_diff.pkl")
df_prepan_pov_age = pd.read_pickle("./df_prepan_pov_age.pkl")
df_posInc_policy = dill.load(open('df_posInc_policy.pkd', 'rb'))

In [132]:
columns = (['popdensity_2018', 'PCT_POV', 'PCT_AGED'])
df_prepan_pov_age_features = df_prepan_pov_age[columns]

In [133]:
df_prepan_pov_age_features.head(3)

popdensity_2018  PCT_POV  PCT_AGED
0        36.113876     12.1  0.145833
1        52.949490     10.1  0.195404
2        10.854899     27.1  0.179738

In [134]:
standard_scaler = StandardScaler()
df_prepan_pov_age_scaled = pd.DataFrame(standard_scaler.fit_transform(df_prepan_pov_age_features),
                                          columns=df_prepan_pov_age_features.columns)

In [135]:
df_prepan_pov_age_scaled.head(3)

popdensity_2018   PCT_POV  PCT_AGED
0        -0.099611 -0.406158  0.049994
1        -0.075433 -0.751041  0.647704
2        -0.135886  2.180469  0.458803

In [136]:
for n_clusters in range(2, 9):
    km = KMeans(n_clusters=n_clusters)
    km.fit(df_prepan_pov_age_scaled)
    
    # Predict the cluster for each data point
    preds = km.predict(df_prepan_pov_age_scaled)

    # Calculate the mean silhouette coefficient for the number of clusters chosen
    score = silhouette_score(df_prepan_pov_age_scaled, preds, metric='euclidean')
    print('For n_clusters = {}, the average silhouette_score is : {}'
          .format(n_clusters, score.round(5)))

For n_clusters = 2, the average silhouette_score is : 0.47422
For n_clusters = 3, the average silhouette_score is : 0.48254
For n_clusters = 4, the average silhouette_score is : 0.45532
For n_clusters = 5, the average silhouette_score is : 0.41241
For n_clusters = 6, the average silhouette_score is : 0.41983
For n_clusters = 7, the average silhouette_score is : 0.37303
For n_clusters = 8, the average silhouette_score is : 0.378


In [183]:
#Determining the clusters

n_clusters = 3
kmeans = KMeans(n_clusters=n_clusters, n_init=10)
kmeans.fit(df_prepan_pov_age_scaled)

cols = kmeans.predict(df_prepan_pov_age_scaled)
colors = ['#ba2121ff', '#42a5f5ff', '#efa016ff']
centroids = kmeans.cluster_centers_

def plot_rotate(az, el):
    fig = plt.figure(figsize=(10,10))
    ax = fig.add_subplot(111, projection='3d')

    ax.view_init(elev=el, azim=az)
    
    x = df_prepan_pov_age_scaled['popdensity_2018']
    y = df_prepan_pov_age_scaled['PCT_POV']
    z = df_prepan_pov_age_scaled['PCT_AGED']
    ax.set_xlabel('Pop. Density (persons/km^2)')
    ax.set_ylabel('Percent in Poverty')
    ax.set_zlabel('Percent of Seniors (Age 65+)', rotation=90, labelpad=-2)

    ax.scatter(x, y, z, marker='o', s=20, color=[colors[col] for col in cols])

clusters_3d_plot = interact(plot_rotate, az=IntSlider(min=0, max=300, step=10, value=50, description='azimith'), 
                      el=IntSlider(min=0, max=90, step=10, value=20, description='elevation'));

clusters_3d_plot

interactive(children=(IntSlider(value=50, description='azimith', max=300, step=10), IntSlider(value=20, descri…

<function __main__.plot_rotate(az, el)>

In [185]:
# Invert standard scaler
true_centers = standard_scaler.inverse_transform(centroids)
typical_counties = pd.DataFrame(true_centers, columns=df_prepan_pov_age_scaled.columns, 
                                 index=['typical county 1', 'typical county 2', 
                                        'typical county 3'])

In [186]:
# DO NOT DELETE: COMMENTED OUT SO CLUSTER ASSIGMENT WON'T RESET

# Assign cluster labels to df_prepan_pov_age

# cluster1 = df_prepan_pov_age_scaled[kmeans.labels_ == 0] 
# cluster2 = df_prepan_pov_age_scaled[kmeans.labels_ == 1] 
# cluster3 = df_prepan_pov_age_scaled[kmeans.labels_ == 2] 

# orig_index_val = df_prepan_pov_age.index.values
# cluster1_index_val = df_prepan_pov_age_scaled[kmeans.labels_ == 0].index.values
# cluster2_index_val = df_prepan_pov_age_scaled[kmeans.labels_ == 1].index.values
# cluster3_index_val = df_prepan_pov_age_scaled[kmeans.labels_ == 2].index.values

# df_prepan_pov_age['Cluster'] = None

# for i in orig_index_val:
#     if i in cluster1_index_val:
#         df_prepan_pov_age['Cluster'][i] = '1'
#     elif i in cluster2_index_val:
#         df_prepan_pov_age['Cluster'][i] = '2' 
#     else:
#         df_prepan_pov_age['Cluster'][i] = '3'

<ipython-input-186-70ceabfd6815>:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_prepan_pov_age['Cluster'][i] = '2'
<ipython-input-186-70ceabfd6815>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_prepan_pov_age['Cluster'][i] = '1'
<ipython-input-186-70ceabfd6815>:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_prepan_pov_age['Cluster'][i] = '3'


In [187]:
# dill.dump(df_prepan_pov_age, open('df_prepan_pov_age_cluster.pkd', 'wb'))

In [182]:
df_prepan_pov_age = dill.load(open('df_prepan_pov_age_cluster.pkd', 'rb'))

In [140]:
# DO NOT DELETE - COMMENTED OUT SO CLUSTERS WON'T BE REASSIGNED

# columns = (['FIPS', 'Cluster'])
# df_clusters = df_prepan_pov_age[columns].rename(columns={'FIPS': 'fips'})
# df_clusters.head(3)

fips Cluster
0  1001       1
1  1003       1
2  1005       1

In [188]:
#dill.dump(df_clusters, open('df_clusters.pkd', 'wb'))

In [189]:
df_clusters = dill.load(open('df_clusters.pkd', 'rb'))

## Checkpoint: 

Following Dataframes are constructed: 
- dataframe with intervention effects:  df_interv_diff
- dataframe with cluster groups included:  df_prepan_pov_age, df_clusters

In [48]:
# Next Steps: 
# Merge Cluster Number to df_interv_diff (df with intervention effects)
# Calculate avg diffs for each intervention for each cluster 

In [190]:
# DO NOT DELETE - COMMENTED OUT TO SAVE MEMORY CLUSTER ASSIGNMENT 

# # Step 1: Merge Cluster Number to df_interv_diff (df with intervention effects)

# df_intervdiff_clusters = pd.merge(df_interv_diff, df_clusters, on='fips')
# df_intervdiff_clusters['fips'] = df_intervdiff_clusters['fips'].map(str)
# df_intervdiff_clusters.head()

stname         ctyname  fips Stay at home/ shelter in place  \
0  Alabama  Autauga County  1001                       2020/4/4   
1  Alabama  Baldwin County  1003                       2020/4/4   
2  Alabama  Barbour County  1005                       2020/4/4   
3  Alabama     Bibb County  1007                       2020/4/4   
4  Alabama   Blount County  1009                       2020/4/4   

  Schools Closed Mask Mandate Restaurants Closed  pre_post_diff_Mask Mandate  \
0      2020/3/20    2020/7/16          2020/3/19                    0.077080   
1      2020/3/20    2020/7/16          2020/3/19                    0.066835   
2      2020/3/20    2020/7/16          2020/3/19                    0.287081   
3      2020/3/20    2020/7/16          2020/3/19                   -0.153061   
4      2020/3/20    2020/7/16          2020/3/19                    0.000000   

   pre_post_diff_Stay at home/ shelter in place  \
0                                     -0.012847   
1                                     -0.019002   
2                                     -0.074641   
3                                     -0.038265   
4                                     -0.014819   

   pre_post_diff_Restaurants Closed Cluster  
0                         -0.012847       1  
1                         -0.021623       1  
2                         -0.045933       1  
3                         -0.044643       1  
4                         -0.014819       1

In [195]:
# dill.dump(df_intervdiff_clusters, open('df_intervdiff_clusters.pkd', 'wb'))

In [19]:
df_intervdiff_clusters = dill.load(open('df_intervdiff_clusters.pkd', 'rb'))

In [20]:
# Test
df_intervdiff_clusters[df_intervdiff_clusters['Cluster']=='2']

stname           ctyname   fips Stay at home/ shelter in place  \
14      Alabama   Cleburne County   1029                       2020/4/4   
18      Alabama      Coosa County   1037                       2020/4/4   
33      Alabama      Henry County   1067                       2020/4/4   
37      Alabama      Lamar County   1075                       2020/4/4   
42      Alabama    Lowndes County   1085                       2020/4/4   
...         ...               ...    ...                            ...   
3076  Wisconsin   Kewaunee County  55061                      2020/3/25   
3084  Wisconsin  Marquette County  55077                      2020/3/25   
3085  Wisconsin  Menominee County  55078                      2020/3/25   
3093  Wisconsin     Pierce County  55093                      2020/3/25   
3135    Wyoming   Sublette County  56035                              0   

     Schools Closed Mask Mandate Restaurants Closed  \
14        2020/3/20    2020/7/16          2020/3/19   
18        2020/3/20    2020/7/16          2020/3/19   
33        2020/3/20    2020/7/16          2020/3/19   
37        2020/3/20    2020/7/16          2020/3/19   
42        2020/3/20    2020/7/16          2020/3/19   
...             ...          ...                ...   
3076      2020/3/18     2020/8/1          2020/3/18   
3084      2020/3/18     2020/8/1          2020/3/18   
3085      2020/3/18     2020/8/1          2020/3/18   
3093      2020/3/18     2020/8/1          2020/3/18   
3135      2020/3/19            0          2020/3/19   

      pre_post_diff_Mask Mandate  \
14                      0.095321   
18                     -0.173322   
33                      0.058109   
37                     -0.051595   
42                      0.014323   
...                          ...   
3076                   -0.021026   
3084                    0.018512   
3085                   -0.030669   
3093                   -0.013428   
3135                         NaN   

      pre_post_diff_Stay at home/ shelter in place  \
14                                        0.028596   
18                                       -0.013332   
33                                       -0.016603   
37                                       -0.010319   
42                                       -0.128907   
...                                            ...   
3076                                     -0.028035   
3084                                     -0.009256   
3085                                      0.000000   
3093                                      0.006714   
3135                                           NaN   

      pre_post_diff_Restaurants Closed Cluster  
14                           -0.057192       2  
18                           -0.053330       2  
33                           -0.066410       2  
37                           -0.051595       2  
42                           -0.128907       2  
...                                ...     ...  
3076                         -0.007009       2  
3084                          0.000000       2  
3085                         -0.030669       2  
3093                         -0.003357       2  
3135                          0.000000       2  

[722 rows x 11 columns]

In [143]:
df_interv_diff.loc[1829,:]  #before clusters

stname                                                 New York
ctyname                                         Allegany County
fips                                                      36003
Stay at home/ shelter in place                        2020/3/22
Schools Closed                                        2020/3/18
Mask Mandate                                          2020/4/17
Restaurants Closed                                    2020/3/17
pre_post_diff_Mask Mandate                           0.00923049
pre_post_diff_Stay at home/ shelter in place         -0.0246146
pre_post_diff_Restaurants Closed                      -0.018461
Name: 1829, dtype: object

In [144]:
df_intervdiff_clusters.loc[1829,:]  #after clusters

stname                                              New York
ctyname                                         Bronx County
fips                                                   36005
Stay at home/ shelter in place                     2020/3/22
Schools Closed                                     2020/3/18
Mask Mandate                                       2020/4/17
Restaurants Closed                                 2020/3/17
pre_post_diff_Mask Mandate                          0.499854
pre_post_diff_Stay at home/ shelter in place       -0.789333
pre_post_diff_Restaurants Closed                    -1.00101
Cluster                                                    3
Name: 1829, dtype: object

In [171]:
# Step 2: Calculate avg diffs for each intervention for each cluster 
df_meandiff = df_intervdiff_clusters.groupby(['Cluster']).mean()
df_meandiff

pre_post_diff_Mask Mandate  \
Cluster                               
1                          0.009243   
2                         -0.039581   
3                          0.306766   

         pre_post_diff_Stay at home/ shelter in place  \
Cluster                                                 
1                                           -0.034795   
2                                           -0.020981   
3                                           -0.449988   

         pre_post_diff_Restaurants Closed  
Cluster                                    
1                               -0.036572  
2                               -0.025076  
3                               -0.704768

## Visualizations

In [172]:
columns = ['pre_post_diff_Mask Mandate', 'pre_post_diff_Stay at home/ shelter in place', 'pre_post_diff_Restaurants Closed']
df_meandiff2 = df_meandiff[columns]
df_meandiff2.reset_index(inplace=True)
df_meandiff2

Cluster  pre_post_diff_Mask Mandate  \
0       1                    0.009243   
1       2                   -0.039581   
2       3                    0.306766   

   pre_post_diff_Stay at home/ shelter in place  \
0                                     -0.034795   
1                                     -0.020981   
2                                     -0.449988   

   pre_post_diff_Restaurants Closed  
0                         -0.036572  
1                         -0.025076  
2                         -0.704768

In [192]:
# Check "Interactively select a y-variable" from notebook; Check Office Hours 4.3, ~51:00 
# df.melt; id_vars is the name of the column I am not touching. value_vars is the name of the columns I want to "melt". As in take those columns, and create a single column out of them.

df_long = df_meandiff2.melt(id_vars='Cluster', value_vars=['pre_post_diff_Mask Mandate', 'pre_post_diff_Stay at home/ shelter in place', 'pre_post_diff_Restaurants Closed'])
df_long.sample(9, random_state=1)

Cluster                                      variable     value
8       3              pre_post_diff_Restaurants Closed -0.704768
2       3                    pre_post_diff_Mask Mandate  0.306766
6       1              pre_post_diff_Restaurants Closed -0.036572
7       2              pre_post_diff_Restaurants Closed -0.025076
1       2                    pre_post_diff_Mask Mandate -0.039581
0       1                    pre_post_diff_Mask Mandate  0.009243
4       2  pre_post_diff_Stay at home/ shelter in place -0.020981
3       1  pre_post_diff_Stay at home/ shelter in place -0.034795
5       3  pre_post_diff_Stay at home/ shelter in place -0.449988

In [193]:
base = alt.Chart(df_long).mark_bar().encode(
    alt.X('Cluster'),
    alt.Y('value', title='Pre/Post Difference (Daily Inc. per 1000 People)')
).properties(
    height=375,
    width=375
)

# A dropdown filter
columns = ['pre_post_diff_Mask Mandate', 'pre_post_diff_Stay at home/ shelter in place', 'pre_post_diff_Restaurants Closed']
column_dropdown = alt.binding_select(options=columns)
column_select = alt.selection_single(
    fields=['variable'],
    on='doubleclick',
    clear=False, 
    bind=column_dropdown, 
    name='y',
    init={'variable': 'pre_post_diff_Mask Mandate'}
)

filter_columns = base.add_selection(
    column_select
).transform_filter(
    column_select
)

filter_columns.interactive()

alt.Chart(...)

## Create comparison Bar Graph (formerly Find statistics for individual county)

In [194]:
df_counties_w_cluster_stats = df_intervdiff_clusters.merge(df_meandiff2, on ='Cluster')
#df_counties_w_cluster_stats[df_counties_w_cluster_stats['Cluster'] == '2'].head()

In [198]:
def make_summary_and_bar_chart(state, county):
    county_formatted = county + " County"
    df_state_filter = df_counties_w_cluster_stats[df_counties_w_cluster_stats['stname'] == state]
    df_county_filter = df_state_filter[df_state_filter['ctyname'] == county_formatted]
    
    columns1 = ['pre_post_diff_Mask Mandate_x', 'pre_post_diff_Stay at home/ shelter in place_x', 'pre_post_diff_Restaurants Closed_x']
    columns2 = ['pre_post_diff_Mask Mandate_y', 'pre_post_diff_Stay at home/ shelter in place_y', 'pre_post_diff_Restaurants Closed_y']

    max_diff = df_county_filter[columns1].max(axis=1).item()

    if max_diff <= 0: 
        print('None of the policies reduced COVID-19 spread in {} State\'s {}.'.format(state, county_formatted))
        for i in columns1:
            split_i = i.split('_')
            if max_diff == df_county_filter[i].item():
                round_max_diff = round(max_diff, 3)
                print('The {} policy was the most effective in slowing COVID-19 spread in {} State\'s {}.'.format(split_i[3], state, county_formatted))
                break
    else: 
        for i in columns1:
            split_i = i.split('_')
            if max_diff == df_county_filter[i].item():
                round_max_diff = round(max_diff, 3)
                print('The {} policy is the most effective intervention in reducing COVID-19 spread in {} State\'s {}. It reduced the spread by {} per 1000 people after 3 weeks post intervention'.format(split_i[3], state, county_formatted, round_max_diff))
                break
            if df_county_filter[i].item() != max_diff and df_county_filter[i].item() > 0: 
                round_item = round(df_county_filter[i].item(), 3)
                print('The {} policy was also effective in reducing COVID-19 spread in {} State\'s {}. It reduced the spread by {} per 1000 people after 3 weeks post intervention'.format(split_i[3], state, county_formatted, round_item))
    #################################################################################################
    row_index_val = list(df_county_filter.index)[0]
    
    df_county_filter_short = df_county_filter[['pre_post_diff_Mask Mandate_x', 
                                           'pre_post_diff_Stay at home/ shelter in place_x', 
                                           'pre_post_diff_Restaurants Closed_x']]

    df_county_filter_short = df_county_filter_short.rename(columns={'pre_post_diff_Mask Mandate_x': 'Mask Mandate', 
                             'pre_post_diff_Stay at home/ shelter in place_x': 'Stay at home/ shelter in place', 
                             'pre_post_diff_Restaurants Closed_x':'Restaurants Closed'})

    df_county_filter_t = df_county_filter_short.transpose().reset_index().rename(columns={row_index_val: 'mean_diff', 'index': 'intervention'})
    df_county_filter_t['level'] = county_formatted 
    #################################################################################################    
    df_cluster_filter_short = df_county_filter[['pre_post_diff_Mask Mandate_y', 
                                           'pre_post_diff_Stay at home/ shelter in place_y', 
                                           'pre_post_diff_Restaurants Closed_y']]

    df_cluster_filter_short = df_cluster_filter_short.rename(columns={'pre_post_diff_Mask Mandate_y': 'Mask Mandate', 
                             'pre_post_diff_Stay at home/ shelter in place_y': 'Stay at home/ shelter in place', 
                             'pre_post_diff_Restaurants Closed_y':'Restaurants Closed'})

    df_cluster_filter_t = df_cluster_filter_short.transpose().reset_index() \
                                            .rename(columns={row_index_val: 'mean_diff', 'index': 'intervention'})
    df_cluster_filter_t['level'] = 'County\'s Cluster' 
    #################################################################################################
    df_intervdiff_clusters_renamed = df_intervdiff_clusters.rename(columns={'pre_post_diff_Mask Mandate': 'Mask Mandate',
                                                                        'pre_post_diff_Stay at home/ shelter in place': 'Stay at home/ shelter in place',
                                                                        'pre_post_diff_Restaurants Closed': 'Restaurants Closed'})
    df_meandiff_all = df_intervdiff_clusters_renamed[['Mask Mandate','Stay at home/ shelter in place','Restaurants Closed']]
    df_all_t = df_meandiff_all.mean().to_frame().reset_index().rename(columns = {0:'mean_diff', 'index': 'intervention'})
    df_all_t['level'] = 'U.S.A.'
    #################################################################################################
    frames = [df_county_filter_t, df_cluster_filter_t, df_all_t]
    total_df_bar = pd.concat(frames)
    #################################################################################################
    bar_chart_compare = alt.Chart(total_df_bar).mark_bar().encode(
        x='level:O',
        y='mean_diff:Q',
        color='level:N',
        column='intervention:N',
        tooltip=['mean_diff:Q']
        ).properties(
            height=500,
            width=100
        ).interactive()
    
    return bar_chart_compare
# May also want to return the print statements 

In [199]:
state = input("Enter your State: ")
county = input("Enter your County: ")
make_summary_and_bar_chart(state, county)

Enter your State: New York
Enter your County: Nassau
The Mask Mandate policy is the most effective intervention in reducing COVID-19 spread in New York State's Nassau County. It reduced the spread by 0.565 per 1000 people after 3 weeks post intervention


alt.Chart(...)

## Create time series line graph comparing county, cluster, and total per intervention. 

In [200]:
df_posInc_policy_clusters = df_posInc_policy.merge(df_clusters, on = 'fips') 

In [201]:
def find_county_SMA(row_idx, intervention): 
    try:
        row_county_fips = df_posInc_policy_clusters['fips'][row_idx]
        row_county = df_posInc_policy_clusters['ctyname'][row_idx]
        row_county_cluster = df_posInc_policy_clusters['Cluster'][row_idx]
        row_event_date = df_posInc_policy_clusters[intervention][row_idx]
        row_county_pop = df_posInc_policy_clusters['POP_ESTIMA'][row_idx]
        row_event_date = datetime.datetime.strptime(row_event_date, '%Y/%m/%d')
        pre_window_start = row_event_date - timedelta(days = 21)
        post_window_start = row_event_date + timedelta(days = 14) # 3 weeks after intervention
        post_window_end = row_event_date + timedelta(days = 21) # 3 weeks after intervention
        
        row_event_date_str = datetime.datetime.strftime(row_event_date, '%Y%m%d')
        pre_window_start_str = datetime.datetime.strftime(pre_window_start, '%Y%m%d')
        post_window_start_str = datetime.datetime.strftime(post_window_start, '%Y%m%d')
        post_window_end_str = datetime.datetime.strftime(post_window_end, '%Y%m%d')
        
        col_row_event_date = 'confirmed_cases_{}'.format(row_event_date_str)
        col_pre_window_start = 'confirmed_cases_{}'.format(pre_window_start_str)
        col_post_window_start = 'confirmed_cases_{}'.format(post_window_start_str)
        col_post_window_end = 'confirmed_cases_{}'.format(post_window_end_str)
        
        df_posInc_policy_window = df_posInc_policy_clusters.loc[row_idx,col_pre_window_start:col_post_window_end].to_frame() \
                                                .reset_index() \
                                                .rename(columns = {row_idx:'total_cases', 'index':'orig_str_date'}) 
        df_posInc_policy_window['fips'] = row_county_fips
        df_posInc_policy_window['ctyname'] = row_county
        df_posInc_policy_window['intervention'] = intervention
        df_posInc_policy_window['daily_increase'] = None
        df_posInc_policy_window['daily_increase_per1000'] = None
        df_posInc_policy_window['days since intervention'] = list(range(-21,22))
        df_posInc_policy_window['cluster'] = row_county_cluster
        
        for row in range(1, len(df_posInc_policy_window)):            
            try: 
                df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
                df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop) 
            except: 
                df_posInc_policy_window['daily_increase'][row] = None
        
        df_posInc_policy_window['SMA_7'] = df_posInc_policy_window.loc[:,'daily_increase_per1000'].rolling(window=7).mean()
        
        df_posInc_policy_window = df_posInc_policy_window[['fips', 'ctyname', 'cluster','intervention', 'days since intervention', 'daily_increase','daily_increase_per1000','SMA_7']]
        df_posInc_policy_window = df_posInc_policy_window[df_posInc_policy_window['days since intervention'] >= -14]
        
        return df_posInc_policy_window
    except: 
        return None
    
    

In [203]:
# DO NOT DELETE - Test Case Code for find_county_SMA(row_idx, intervention)

# row_idx = 0
# intervention = 'Mask Mandate'
# df_county_SMA = find_county_SMA(row_idx, intervention)
# df_county_SMA

In [205]:
# DO NOT DELETE; COMMENTING OUT TO PREVENT FROM RUNNING WHEN RUN ALL 

# interventions = ['Mask Mandate', 'Schools Closed', 'Restaurants Closed']

# df_all_SMA_7 = pd.DataFrame(columns = ['fips','ctyname','cluster','intervention','days since intervention','daily_increase','daily_increase_per1000','SMA_7'])

# for row_idx in range(len(df_posInc_policy)):
#     if row_idx % 500 == 0:
#         print(row_idx, " out of ", len(df_posInc_policy))
#     for interv in interventions: 
#         df = find_county_SMA(row_idx, interv)
#         df_all_SMA_7 = pd.concat([df_all_SMA_7, df])

# df_all_SMA_7



0  out of  3142


<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

...

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase'][row] = df_posInc_policy_window.loc[row,'total_cases'] - df_posInc_policy_window.loc[row-1,'total_cases']
<ipython-input-201-312a2b26ce6b>:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_posInc_policy_window['daily_increase_per1000'][row] = df_posInc_policy_window['daily_increase'][row] *(1000 / row_county_pop)
<ipython-input-201-312a2b26ce6b>:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.py

fips         ctyname cluster        intervention days since intervention  \
7    1001  Autauga County       1        Mask Mandate                     -14   
8    1001  Autauga County       1        Mask Mandate                     -13   
9    1001  Autauga County       1        Mask Mandate                     -12   
10   1001  Autauga County       1        Mask Mandate                     -11   
11   1001  Autauga County       1        Mask Mandate                     -10   
..    ...             ...     ...                 ...                     ...   
38  56045   Weston County       1  Restaurants Closed                      17   
39  56045   Weston County       1  Restaurants Closed                      18   
40  56045   Weston County       1  Restaurants Closed                      19   
41  56045   Weston County       1  Restaurants Closed                      20   
42  56045   Weston County       1  Restaurants Closed                      21   

   daily_increase daily_increase_per1000     SMA_7  
7               8               0.143882  0.197838  
8              14               0.251794  0.215823  
9              17                0.30575  0.246655  
10             19                0.34172  0.236378  
11              3              0.0539559  0.218393  
..            ...                    ...       ...  
38              0                      0  0.000000  
39              0                      0  0.000000  
40              0                      0  0.000000  
41              0                      0  0.000000  
42              0                      0  0.000000  

[299988 rows x 8 columns]

In [206]:
dill.dump(df_all_SMA_7, open('df_all_SMA_7.pkd', 'wb'))

In [2]:
df_all_SMA_7 = dill.load(open('df_all_SMA_7.pkd', 'rb'))

In [89]:
# df2 = df_all_SMA_7[df_all_SMA_7['intervention']=='Mask Mandate']
# df2 = df2[df2['cluster']=='1']
# df2['fips'].unique()

array([1001, 1003, 1005, ..., 55137, 55139, 55141], dtype=object)

In [6]:
df_state_fips = df_posInc_policy[['fips','stname']]
df_all_SMA_7 = df_all_SMA_7.merge(df_state_fips, on='fips') 

df_all_SMA_7.head()

fips         ctyname cluster  intervention days since intervention  \
0  1001  Autauga County       1  Mask Mandate                     -14   
1  1001  Autauga County       1  Mask Mandate                     -13   
2  1001  Autauga County       1  Mask Mandate                     -12   
3  1001  Autauga County       1  Mask Mandate                     -11   
4  1001  Autauga County       1  Mask Mandate                     -10   

  daily_increase daily_increase_per1000     SMA_7   stname  
0              8               0.143882  0.197838  Alabama  
1             14               0.251794  0.215823  Alabama  
2             17                0.30575  0.246655  Alabama  
3             19                0.34172  0.236378  Alabama  
4              3              0.0539559  0.218393  Alabama

In [15]:
def find_county_SMA(state, county, intervention):
    df_filtered = df_all_SMA_7[df_all_SMA_7['stname']==state]
    df_filtered = df_filtered[df_filtered['ctyname']==county]
    df_filtered = df_filtered[df_filtered['intervention']==intervention]
    df_county_SMA = df_filtered.groupby(['days since intervention']).mean().reset_index() \
                                .rename(columns={'SMA_7': '{}_SMA'.format(county)})
    return df_county_SMA    
####################################################################################################
def find_cluster_SMA(cluster, intervention):
    df_filtered = df_all_SMA_7[df_all_SMA_7['cluster']==cluster] 
    df_filtered = df_filtered[df_filtered['intervention']==intervention]
    df_cluster_SMA_7 = df_filtered.groupby(['days since intervention']).mean().reset_index() \
                                .rename(columns={'SMA_7': 'Cluster_{}_SMA'.format(cluster)})
    return df_cluster_SMA_7

####################################################################################################
def find_all_SMA(intervention):
    df_filtered = df_all_SMA_7[df_all_SMA_7['intervention']==intervention]
    df_all_SMA = df_filtered.groupby(['days since intervention']).mean().reset_index() \
                                .rename(columns={'SMA_7': 'all_SMA'})
    return df_all_SMA
####################################################################################################
def get_cluster_label(state, county):
    county = county + " County"
    df_temp = df_all_SMA_7[df_all_SMA_7['stname']==state]
    df_temp = df_temp[df_temp['ctyname']==county]
    cluster = df_temp.iloc[0]['cluster']
    return cluster
####################################################################################################
def multi_line_graph(state, county, intervention):
    cluster = get_cluster_label(state, county)
    county = county + " County"
    df_county_SMA = find_county_SMA(state, county, intervention)
    df_cluster_SMA = find_cluster_SMA(cluster, intervention)
    df_all_SMA = find_all_SMA(intervention)
    df_merged = df_county_SMA.merge(df_cluster_SMA.merge(df_all_SMA, on='days since intervention'), on='days since intervention')
    data = df_merged.melt('days since intervention')
    
    chart_one = alt.Chart(data, title="SMA ({} vs. Cluster {} vs. All)".format(county, cluster)).mark_line(point=True).encode(
    x='days since intervention',
    y=alt.Y('value', title='SMA (New Cases per 1000 People)'),
    color='variable',
    tooltip = ['days since intervention:Q', 'value:Q']
    ).interactive()

    return chart_one

In [21]:
# Testing multi_line_graph()

state = input("Enter State: ")
county = input("Enter County: ")
intervention = 'Mask Mandate'

multi_line_graph(state, county, intervention)

Enter State: Wisconsin
Enter County: Kewaunee


alt.Chart(...)